# Make a DF with 1s and 0s for whether or not that link is included at that timestamp

### 1 - English outlink history first

In [2]:
import numpy as np
import pandas as pd
import wikifunctions as wf #Brian's stuff

from collections import Counter

from urllib.parse import unquote

import seaborn as sns
import matplotlib.pyplot as plt
import datetime

import pickle

ModuleNotFoundError: No module named 'bs4'

### functions i need

In [2]:
import itertools


def merge(*lists):
    newlist = []
    for i in lists:
            newlist.extend(i)
    return newlist

## English outlink history first

In [3]:
#get all of the page revisions

en_rev_df = wf.get_all_page_revisions('Arab Spring')

In [5]:
en_rev_df

revid    parentid           user    userid  \
0      410393753           0         Jmj713   4589092   
1      410405823   410393753         Jmj713   4589092   
2      410406936   410405823         Jmj713   4589092   
3      410407396   410406936         Jmj713   4589092   
4      410413036   410407396         Jmj713   4589092   
...          ...         ...            ...       ...   
9933  1188823099  1187072775  158.143.9.215         0   
9934  1188823483  1188823099        Skitash  44840730   
9935  1190279584  1188823483   Citation bot   7903804   
9936  1191794174  1190279584     Октябрь123  47104481   
9937  1192245355  1191794174          Dsp13   1752894   

                     timestamp    size  \
0    2011-01-27 16:55:08+00:00     822   
1    2011-01-27 18:01:13+00:00     936   
2    2011-01-27 18:07:38+00:00     999   
3    2011-01-27 18:10:05+00:00    1094   
4    2011-01-27 18:43:56+00:00    1168   
...                        ...     ...   
9933 2023-12-07 22:34:07+00:00  282516   
9934 2023-12-07 22:36:44+00:00  282512   
9935 2023-12-17 00:29:55+00:00  282541   
9936 2023-12-25 21:24:39+00:00  282524   
9937 2023-12-28 11:35:28+00:00  282548   

                                          sha1  \
0     cb89ac8f03c78acd30186e37f8c5280000201347   
1     60514406d46c7f7ff92c0863af12a0204c167d8b   
2     a2ab6330b31fc8b41539bee02f4ed2222159d83d   
3     23dd3ad50ee8431094e311d323b3a08e19c6ca5d   
4     a9302194b9f68fefdabd3f379185c2e07392b399   
...                                        ...   
9933  4e2a0c4d6e12ffa54a69dc55001e697937a7b8e4   
9934  936c3bfffe6285aa04e46eb232843677a4a292f2   
9935  632df02b0250b1e02648c8c18b98e93258dde64d   
9936  0f334764a49cab1067db13adcbbc42a258c206b0   
9937  4d25dbad25cba10b2583385c9cbc9f5b8dab48da   

                                                comment  anon userhidden  \
0     [[WP:AES|←]]Created page with 'The '''2010–201...   NaN        NaN   
1                                                         NaN        NaN   
2                                                         NaN        NaN   
3                                                         NaN        NaN   
4                                                         NaN        NaN   
...                                                 ...   ...        ...   
9933                                       /* Causes */  True        NaN   
9934  Undid revision 1188823099 by [[Special:Contrib...   NaN        NaN   
9935  Add: bibcode. | [[:en:WP:UCB|Use this bot]]. [...   NaN        NaN   
9936                                    /* Etymology */   NaN        NaN   
9937                                              wlink   NaN        NaN   

     sha1hidden commenthidden         page        date   diff       lag  \
0           NaN           NaN  Arab Spring  2011-01-27    NaN       NaN   
1           NaN           NaN  Arab Spring  2011-01-27  114.0    3965.0   
2           NaN           NaN  Arab Spring  2011-01-27   63.0     385.0   
3           NaN           NaN  Arab Spring  2011-01-27   95.0     147.0   
4           NaN           NaN  Arab Spring  2011-01-27   74.0    2031.0   
...         ...           ...          ...         ...    ...       ...   
9933        NaN           NaN  Arab Spring  2023-12-07    4.0  914855.0   
9934        NaN           NaN  Arab Spring  2023-12-07   -4.0     157.0   
9935        NaN           NaN  Arab Spring  2023-12-17   29.0  784391.0   
9936        NaN           NaN  Arab Spring  2023-12-25  -17.0  766484.0   
9937        NaN           NaN  Arab Spring  2023-12-28   24.0  223849.0   

              age  
0        0.000000  
1        0.045891  
2        0.050347  
3        0.052049  
4        0.075556  
...           ...  
9933  4697.235405  
9934  4697.237222  
9935  4706.315822  
9936  4715.187164  
9937  4717.778009  

[9938 rows x 17 columns]

In [4]:
en_freq_revids = en_rev_df.groupby(pd.Grouper(key='timestamp',freq='M')).agg({'revid':'min'})['revid']

outlinks = {}

for _revid in en_freq_revids.values:
    outlinks[_revid] = wf.get_revision_outlinks(_revid)

In [7]:
en_freq_revids

timestamp
2011-01-31 00:00:00+00:00     410393753
2011-02-28 00:00:00+00:00     411278546
2011-03-31 00:00:00+00:00     416471292
2011-04-30 00:00:00+00:00     421746845
2011-05-31 00:00:00+00:00     426865693
                                ...    
2023-08-31 00:00:00+00:00    1168891916
2023-09-30 00:00:00+00:00    1174011981
2023-10-31 00:00:00+00:00    1179318598
2023-11-30 00:00:00+00:00    1183083811
2023-12-31 00:00:00+00:00    1188823099
Freq: M, Name: revid, Length: 156, dtype: int64

In [5]:
# resolve redirects

for i in outlinks:
    outlinks[i] = wf.resolve_redirects(outlinks[i])
#     print(outlinks[i])
    

In [7]:
import pickle

with open('02c_en_as_rev_outlinks_m.pkl', 'wb') as f:
    pickle.dump(outlinks, f)

In [8]:
with open('02c_en_as_rev_time_m.pkl', 'wb') as f:
    pickle.dump(en_freq_revids, f)

In [9]:
# type(en_freq_revids)

pandas.core.series.Series

## make outlink Dataframe

In [221]:
#https://blog.quantinsti.com/creating-heatmap-using-python-seaborn/
# https://www.askpython.com/python/examples/heatmaps-in-python

In [3]:
import pickle

with open("02c_en_as_rev_outlinks_m.pkl", 'rb') as pickleFile:
    outlinks = pickle.load(pickleFile)

### trial

In [222]:
# make a matrix with 1 and 0 on whether or not the word is included in the time
# column is the word - y 
# row is the time - x

In [11]:
#trial wiht the first one 
first = outlinks[410393753]
second = outlinks[411278546]

#make everything you unique
first_unique = np.unique(first)
second_unique = np.unique(second)
print('first-----', first_unique)
# print('second-----', second_unique)

first----- ['2010–2012 Algerian protests' '2011 Egyptian revolution' 'Algeria'
 'Egypt' 'Jordan' 'Middle East' 'Political demonstration' 'Protest'
 'Tunisia' 'Tunisian Revolution' 'Yemen']


In [12]:
#make a 1 and 0 matrix about the inclusion of those words in that timestamp
#https://stackoverflow.com/questions/63033720/how-can-i-mark-1-0-at-index-in-a-list-with-reference-to-another-list

output = [1 if r in second else 0 for r in first]
output

[1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1]

### work 

In [4]:
#make a unique outlinks dict

outlinksUnique = {}
keys = outlinks.keys()

for i in keys:
    outlinksUnique[i] = np.unique(outlinks[i]).tolist()

In [5]:
outlinksUnique

{410393753: ['2010–2012 Algerian protests',
  '2011 Egyptian revolution',
  'Algeria',
  'Egypt',
  'Jordan',
  'Middle East',
  'Political demonstration',
  'Protest',
  'Tunisia',
  'Tunisian Revolution',
  'Yemen'],
 411278546: ['2010–2012 Algerian protests',
  '2011 Egyptian revolution',
  '2011 South Sudanese independence referendum',
  '2011–2012 Jordanian protests',
  '2012 Egyptian presidential election',
  'Al Arabiya',
  'Al Jazeera',
  'Al-Hasakah',
  'Algeria',
  'Algiers',
  'Ali Abdullah Saleh',
  'Arab states of the Persian Gulf',
  'Arab world',
  'Bashar al-Assad',
  'Bordj Menaïel',
  'Boukhadra',
  'Béjaïa',
  'CASE 30',
  'Civil liberties',
  'Constitution of Yemen',
  'Copycat suicide',
  'Domino theory',
  'Egypt',
  'Egyptian Revolution',
  'Facebook',
  'Friday prayer',
  'Government of Syria',
  'Hasan Al-Turabi',
  'Hosni Mubarak',
  'Human rights in Yemen',
  'Jeddah',
  'Jizan',
  'Jordan',
  'Khartoum',
  'Kurdish',
  'Left-wing politics',
  'Libya',
  'Mau

In [6]:
#make list of all of the unique outlinks used througout time
#this is only a list of outlinks to be later used for the df and heat map
import itertools


def merge(*lists):
    newlist = []
    for i in lists:
            newlist.extend(i)
    return newlist

everyOutlink = merge(outlinks.values()) #makes lists of lists
everyOutlink = list(itertools.chain.from_iterable(everyOutlink)) #puts them all in one list
everyOutlink = np.unique(everyOutlink).tolist() #a list of alphabetized unique outlinks

len(everyOutlink)

837

In [7]:
#go through and create a new dictionary with ones and values correlating to everyOutlink

binaryRevOutlinkDict = {}
keys = outlinksUnique.keys()

for rev in keys:
    binaryRevOutlinkDict[rev] = [1 if r in outlinksUnique[rev] else 0 for r in everyOutlink]


In [8]:
binaryRevOutlinkDict

{410393753: [0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,

In [9]:
#make a df with everything

#make a df
df = pd.DataFrame.from_dict(binaryRevOutlinkDict, orient='index', columns=everyOutlink )
df.reset_index(inplace=True) #make the revision ids a column 

#change name
names = df.columns.tolist()
names[names.index('index')] = 'revs_id'
df.columns = names

# df.head()

In [10]:
df.head()

revs_id  15 October 2011 global protests  2000s energy crisis  \
0  410393753                                0                    0   
1  411278546                                0                    0   
2  416471292                                0                    0   
3  421746845                                0                    0   
4  426865693                                0                    0   

   2004–05 Palestinian local elections  2005 Ahvaz unrest  \
0                                    0                  0   
1                                    0                  0   
2                                    1                  0   
3                                    0                  0   
4                                    0                  0   

   2005 Palestinian presidential election  \
0                                       0   
1                                       0   
2                                       1   
3                                       0   
4                                       0   

   2006 Palestinian legislative election  2007–2008 world food price crisis  \
0                                      0                                  0   
1                                      0                                  0   
2                                      1                                  1   
3                                      0                                  1   
4                                      0                                  1   

   2008 Armenian presidential election  \
0                                    0   
1                                    0   
2                                    0   
3                                    0   
4                                    1   

   2009 Iranian presidential election protests  ...  YouTube  Youth  \
0                                            0  ...        0      0   
1                                            0  ...        0      0   
2                                            1  ...        0      0   
3                                            1  ...        0      0   
4                                            1  ...        1      0   

   Youthquake  Youthquake (movement)  Yoweri Museveni  Zaydism  \
0           0                      0                0        0   
1           0                      0                0        0   
2           0                      0                1        0   
3           1                      0                0        0   
4           1                      0                0        0   

   Zeynep Tufekci  Zimbabwe  Zine El Abidine Ben Ali  Zouérat  
0               0         0                        0        0  
1               0         0                        1        0  
2               0         1                        1        0  
3               0         0                        1        1  
4               0         0                        1        1  

[5 rows x 838 columns]

In [18]:
#clean up timestamp information
times = en_freq_revids.index

times = times.date #making it so its just the date

df['timestamp'] = times #add the timestamps
df['timestamp'] = pd.to_datetime(df['timestamp']) #stuff you have to do bc its a different format
df.set_index("timestamp", inplace=True, drop=True)


df

revs_id  15 October 2011 global protests  2000s energy crisis  \
timestamp                                                                      
2011-01-31   410393753                                0                    0   
2011-02-28   411278546                                0                    0   
2011-03-31   416471292                                0                    0   
2011-04-30   421746845                                0                    0   
2011-05-31   426865693                                0                    0   
...                ...                              ...                  ...   
2023-06-30  1160397894                                0                    0   
2023-07-31  1163298599                                0                    0   
2023-08-31  1168891916                                0                    0   
2023-09-30  1174011981                                0                    0   
2023-10-31  1179318598                                0                    0   

            2004–05 Palestinian local elections  2005 Ahvaz unrest  \
timestamp                                                            
2011-01-31                                    0                  0   
2011-02-28                                    0                  0   
2011-03-31                                    1                  0   
2011-04-30                                    0                  0   
2011-05-31                                    0                  0   
...                                         ...                ...   
2023-06-30                                    0                  0   
2023-07-31                                    0                  0   
2023-08-31                                    0                  0   
2023-09-30                                    0                  0   
2023-10-31                                    0                  0   

            2005 Palestinian presidential election  \
timestamp                                            
2011-01-31                                       0   
2011-02-28                                       0   
2011-03-31                                       1   
2011-04-30                                       0   
2011-05-31                                       0   
...                                            ...   
2023-06-30                                       0   
2023-07-31                                       0   
2023-08-31                                       0   
2023-09-30                                       0   
2023-10-31                                       0   

            2006 Palestinian legislative election  \
timestamp                                           
2011-01-31                                      0   
2011-02-28                                      0   
2011-03-31                                      1   
2011-04-30                                      0   
2011-05-31                                      0   
...                                           ...   
2023-06-30                                      0   
2023-07-31                                      0   
2023-08-31                                      0   
2023-09-30                                      0   
2023-10-31                                      0   

            2007–2008 world food price crisis  \
timestamp                                       
2011-01-31                                  0   
2011-02-28                                  0   
2011-03-31                                  1   
2011-04-30                                  1   
2011-05-31                                  1   
...                                       ...   
2023-06-30                                  0   
2023-07-31                                  0   
2023-08-31                                  0   
2023-09-30                                  0   
2023-10-31                                  0   

            2008 Armenian presid

In [19]:
#get rid of revision ids and transpose, switching the axes makes the heat map easier to read
data = df.iloc[: , 1:] #drop revs_id

data = data.transpose() #flip
data.index.name = None

data

timestamp                               2011-01-31  2011-02-28  2011-03-31  \
15 October 2011 global protests                  0           0           0   
2000s energy crisis                              0           0           0   
2004–05 Palestinian local elections              0           0           1   
2005 Ahvaz unrest                                0           0           0   
2005 Palestinian presidential election           0           0           1   
...                                            ...         ...         ...   
Zaydism                                          0           0           0   
Zeynep Tufekci                                   0           0           0   
Zimbabwe                                         0           0           1   
Zine El Abidine Ben Ali                          0           1           1   
Zouérat                                          0           0           0   

timestamp                               2011-04-30  2011-05-31  2011-06-30  \
15 October 2011 global protests                  0           0           0   
2000s energy crisis                              0           0           0   
2004–05 Palestinian local elections              0           0           0   
2005 Ahvaz unrest                                0           0           0   
2005 Palestinian presidential election           0           0           0   
...                                            ...         ...         ...   
Zaydism                                          0           0           0   
Zeynep Tufekci                                   0           0           0   
Zimbabwe                                         0           0           0   
Zine El Abidine Ben Ali                          1           1           1   
Zouérat                                          1           1           1   

timestamp                               2011-07-31  2011-08-31  2011-09-30  \
15 October 2011 global protests                  0           0           0   
2000s energy crisis                              0           0           0   
2004–05 Palestinian local elections              0           0           0   
2005 Ahvaz unrest                                0           0           0   
2005 Palestinian presidential election           0           0           0   
...                                            ...         ...         ...   
Zaydism                                          0           0           0   
Zeynep Tufekci                                   0           0           0   
Zimbabwe                                         0           0           0   
Zine El Abidine Ben Ali                          1           1           1   
Zouérat                                          1           1           1   

timestamp                               2011-10-31  ...  2023-01-31  \
15 October 2011 global protests                  0  ...           0   
2000s energy crisis                              0  ...           0   
2004–05 Palestinian local elections              0  ...           0   
2005 Ahvaz unrest                                0  ...           0   
2005 Palestinian presidential election           0  ...           0   
...                                            ...  ...         ...   
Zaydism                                          0  ...           1   
Zeynep Tufekci                                   0  ...           1   
Zimbabwe                                         0  ...           0   
Zine El Abidine Ben Ali                          1  ...           1   
Zouérat                                          1  ...           0   

timestamp                               2023-02-28  2023-03-31  2023-04-30  \
15 October 2011 global protests                  0           0           0   
2000s energy crisis                              0           0           0   
2004–05 Palestinian local elections              0           0           0   
2005 Ahvaz unrest       

In [34]:
with open('02c_outlinkInclusiondf_en.pkl', 'wb') as f:
    pickle.dump(data, f)

In [274]:
# #make heatmap
# #going to break it up int 8ish images of 149/100
# #149 timestamps
# #836 outlinks
# #https://seaborn.pydata.org/generated/seaborn.heatmap.html
# plt.style.use("seaborn")

# # fig, ax = plt.subplots(figsize=(10, 5))
# plt.figure(figsize = (13,13))
# heat_map = sns.heatmap(data.iloc[500:549], yticklabels = True) #first 100 columns
# plt.title("Outlinks Through Time(801-837)")
# plt.savefig("801_837outlinkHeatmap.png")
# plt.show()

In [2]:
with open('02c_outlinkInclusiondf_en.pkl', 'rb') as pickleFile:
    df = pickle.load(pickleFile)

In [43]:
df = df.transpose() #flip
df.head()

15 October 2011 global protests  2000s energy crisis  \
timestamp                                                          
2011-01-31                                0                    0   
2011-02-28                                0                    0   
2011-03-31                                0                    0   
2011-04-30                                0                    0   
2011-05-31                                0                    0   

            2004–05 Palestinian local elections  2005 Ahvaz unrest  \
timestamp                                                            
2011-01-31                                    0                  0   
2011-02-28                                    0                  0   
2011-03-31                                    1                  0   
2011-04-30                                    0                  0   
2011-05-31                                    0                  0   

            2005 Palestinian presidential election  \
timestamp                                            
2011-01-31                                       0   
2011-02-28                                       0   
2011-03-31                                       1   
2011-04-30                                       0   
2011-05-31                                       0   

            2006 Palestinian legislative election  \
timestamp                                           
2011-01-31                                      0   
2011-02-28                                      0   
2011-03-31                                      1   
2011-04-30                                      0   
2011-05-31                                      0   

            2007–2008 world food price crisis  \
timestamp                                       
2011-01-31                                  0   
2011-02-28                                  0   
2011-03-31                                  1   
2011-04-30                                  1   
2011-05-31                                  1   

            2008 Armenian presidential election  \
timestamp                                         
2011-01-31                                    0   
2011-02-28                                    0   
2011-03-31                                    0   
2011-04-30                                    0   
2011-05-31                                    1   

            2009 Iranian presidential election protests  \
timestamp                                                 
2011-01-31                                            0   
2011-02-28                                            0   
2011-03-31                                            1   
2011-04-30                                            1   
2011-05-31                                            1   

            2010 Kyrgyz Revolution  ...  YouTube  Youth  Youthquake  \
timestamp                           ...                               
2011-01-31                       0  ...        0      0           0   
2011-02-28                       0  ...        0      0           0   
2011-03-31                       0  ...        0      0           0   
2011-04-30                       0  ...        0      0           1   
2011-05-31                       0  ...        1      0           1   

            Youthquake (movement)  Yoweri Museveni  Zaydism  Zeynep Tufekci  \
timestamp                                                                     
2011-01-31                      0                0        0               0   
2011-02-28                      0                0        0               0   
2011-03-31                      0                1        0               0   
2011-04-30                      0                0        0               0   
2011-05-31                      0                0        0               0   

            Zimbabwe  Zine El Abidine Ben Ali  Zouérat  
timestamp                                               
2011-01-31 

In [44]:
pd.set_option('display.max_rows', None)
print(df.columns)

Index(['15 October 2011 global protests', '2000s energy crisis',
       '2004–05 Palestinian local elections', '2005 Ahvaz unrest',
       '2005 Palestinian presidential election',
       '2006 Palestinian legislative election',
       '2007–2008 world food price crisis',
       '2008 Armenian presidential election',
       '2009 Iranian presidential election protests', '2010 Kyrgyz Revolution',
       ...
       'YouTube', 'Youth', 'Youthquake', 'Youthquake (movement)',
       'Yoweri Museveni', 'Zaydism', 'Zeynep Tufekci', 'Zimbabwe',
       'Zine El Abidine Ben Ali', 'Zouérat'],
      dtype='object', length=837)


In [64]:
lyst  = ['Baba Amr', 'Deep state', "Coup d'état", 'Islah', 'Modernization theory', 'Relative deprivation', 'Palestinian territories', 'Somalia', 'Fouad Hussein', 'Interventionism (politics)', 'Middle East', '2011 Indian anti-corruption movement', 'Anna Hazare', 'Parliament of India', 'The Lokpal and Lokayuktas Act, 2013', 'Youth', 'Climate change', 'Houthi takeover in Yemen', 'Intifada', 'Constitution of Tunisia', 'Standard Moroccan Amazigh', '2011 Israeli social justice protests', 'June 2013 Egyptian protests', 'Gezi Park protests', 'Misrata District', 'The Daily Telegraph', 'Skype', 'December 17', 'January 4', 'Palestine 194', "Ba'athist Iraq", 'Kuwait City', 'Kuwaiti dinar', 'Fez', 'Anti-Americanism', 'Anti-Western sentiment', 'Anti-Zionism', 'Cuban Revolution', 'Conservatism in the United States', 'Al Jazeera English', 'Customs and Border Protection', 'Gulf states', 'Wisner', 'Kurdish languages', 'Julian Assange', 'United Nations General Assembly', 'Arab wedding', 'Kosovo', 'Moshe Dayan Center for Middle Eastern and African Studies', 'David Ignatius', 'War', 'Azaz', 'Human Rights Watch', 'Adam Smith', 'Economist', 'Al-Khalidiya', 'CASE 30', 'Copycat suicide', 'Egyptian Revolution', 'Kurdish', 'War on terror', 'Western Asia', 'Douma, Syria', 'Secularism', 'Tunis', '2000s energy crisis', 'Arab Spring concurrent incidents', 'Demographic trap', 'Economic freedom', 'Mutiny', 'Silent protest', 'Civil disobedience', 'Defection', 'Election', 'Employment', 'Internet activism', 'Kleptocracy', 'Protest camp', 'Sectarianism', 'Sit-in', 'Strike action', 'Urban warfare', 'Adam Roberts (scholar)', 'Andrew Reynolds (political scientist)', 'Armed Forces & Society', 'BBC', 'CNN', 'Carnegie Endowment for International Peace', 'Council on Foreign Relations', 'Der Spiegel', 'Digital object identifier', 'Financial Times', 'Foreign Affairs', 'Hürriyet Daily News', 'ISBN', 'Interface: A Journal for and About Social Movements', 'International Standard Serial Number', 'Jack Goldstone', 'Jadaliyya', 'Peer review', 'Pluto Press', 'Qantara.de', 'Research Papers in Economics', 'Robert Pelletreau', 'Robert Struble Jr.', 'Ruaridh Arrow', 'Semantic Scholar', 'Social Science Research Network', 'The Guardian', 'The National (Abu Dhabi)', 'The New York Times', 'Timothy Garton Ash', 'Reuters', 'Alexander Cockburn', 'CounterPunch', 'Literal translation', 'Rebellion', 'Nonviolent resistance', 'Tripoli, Libya', '2019 Gaza economic protests', "2019 Sudanese coup d'état", 'Khartoum massacre', 'Saddam Hussein', 'Sudanese Revolution', 'Sudanese transition to democracy', 'Transitional Sovereignty Council', 'Insurgency', 'Jamal Khashoggi', 'Prime Minister of Iraq']

In [59]:
# df.iloc(df['Zaydism'])
# , 'Second Libyan Civil War'

row = df['Western Sahara']
print(row)

timestamp
2011-01-31    0
2011-02-28    0
2011-03-31    0
2011-04-30    1
2011-05-31    1
2011-06-30    1
2011-07-31    1
2011-08-31    1
2011-09-30    1
2011-10-31    1
2011-11-30    1
2011-12-31    1
2012-01-31    1
2012-02-29    1
2012-03-31    1
2012-04-30    1
2012-05-31    1
2012-06-30    1
2012-07-31    1
2012-08-31    1
2012-09-30    1
2012-10-31    1
2012-11-30    1
2012-12-31    1
2013-01-31    1
2013-02-28    1
2013-03-31    1
2013-04-30    1
2013-05-31    1
2013-06-30    1
2013-07-31    0
2013-08-31    1
2013-09-30    1
2013-10-31    1
2013-11-30    1
2013-12-31    1
2014-01-31    1
2014-02-28    1
2014-03-31    1
2014-04-30    1
2014-05-31    0
2014-06-30    0
2014-07-31    0
2014-08-31    0
2014-09-30    0
2014-10-31    0
2014-11-30    0
2014-12-31    0
2015-01-31    0
2015-02-28    0
2015-03-31    0
2015-04-30    0
2015-05-31    0
2015-06-30    0
2015-07-31    0
2015-08-31    0
2015-09-30    0
2015-10-31    0
2015-11-30    0
2015-12-31    0
2016-01-31    0
2016-02-29    

In [65]:
df2 = pd.DataFrame()
for i in lyst:
#     print(i)
#     row = df[i]
#     df2.assign(i = row)
# #     df2.loc[row]
# #     print(row)
    extracted_col = df[i]
    df2 = pd.concat([df2, extracted_col.rename(i)], axis=1)


KeyError: 'Western Asia'

In [67]:
df3 = df2.transpose()

In [69]:
pd.set_option('display.max_columns', None)

df3

2011-01-31 00:00:00  \
Baba Amr                                                              0   
Deep state                                                            0   
Coup d'état                                                           0   
Islah                                                                 0   
Modernization theory                                                  0   
Relative deprivation                                                  0   
Palestinian territories                                               0   
Somalia                                                               0   
Fouad Hussein                                                         0   
Interventionism (politics)                                            0   
Middle East                                                           1   
2011 Indian anti-corruption movement                                  0   
Anna Hazare                                                           0   
Parliament of India                                                   0   
The Lokpal and Lokayuktas Act, 2013                                   0   
Youth                                                                 0   
Climate change                                                        0   
Houthi takeover in Yemen                                              0   
Intifada                                                              0   
Constitution of Tunisia                                               0   
Standard Moroccan Amazigh                                             0   
2011 Israeli social justice protests                                  0   
June 2013 Egyptian protests                                           0   
Gezi Park protests                                                    0   
Misrata District                                                      0   
The Daily Telegraph                                                   0   
Skype                                                                 0   
December 17                                                           0   
January 4                                                             0   
Palestine 194                                                         0   
Ba'athist Iraq                                                        0   
Kuwait City                                                           0   
Kuwaiti dinar                                                         0   
Fez                                                                   0   
Anti-Americanism                                                      0   
Anti-Western sentiment                                                0   
Anti-Zionism                                                          0   
Cuban Revolution                                                      0   
Conservatism in the United States                                     0   
Al Jazeera English                                                    0   
Customs and Border Protection                                         0   
Gulf states                                                           0   
Wisner                                                                0   
Kurdish languages                                                     0   
Julian Assange                                                        0   
United Nations General Assembly                                       0   
Arab wedding                                                          0   
Kosovo                                                                0   
Moshe Dayan Center for Middle Eastern and Afric...                    0   
David Ignatius                                                        0   
War                                                                   0   
Azaz                                                                  0   
Human Rights Watch                                                    0   
Ad

## Arabic Outlinks

In [24]:
#get all of the page revisions

ar_rev_df = wf.get_all_page_revisions('الربيع العربي', endpoint='ar.wikipedia.org/w/api.php')

In [25]:
ar_rev_df.head()

revid  parentid           user  userid                 timestamp  size  \
0  6345923         0   عباد ديرانية  216353 2011-02-01 09:13:50+00:00  4478   
1  6345926   6345923   عباد ديرانية  216353 2011-02-01 09:14:28+00:00  4484   
2  6345946   6345926  WikitanvirBot  313683 2011-02-01 09:18:59+00:00  4523   
3  6346126   6345946     Luckas-bot  132596 2011-02-01 10:13:35+00:00  4596   
4  6346182   6346126      CipherBot  147476 2011-02-01 10:31:16+00:00  4640   

                                       sha1  \
0  515f138e10e7f772a9cba75c8b4ca427a0c42949   
1  dac8b6828c4509726b66e3ba0c3f56fd59cf5646   
2  86a1fb8cbc65c67d35e4730585bf12c331102219   
3  672ca5a9b06828a3686acec2622f23268dd42c66   
4  fb0d518bb56fc8828af8bed408b2833e420ad214   

                                             comment anon           page  \
0                                  بذرة قيد التطوير.  NaN  الربيع العربي   
1                                                     NaN  الربيع العربي   
2  r2.7.1) (روبوت إضافة: [[en:2010–2011 Arab worl...  NaN  الربيع العربي   
3  r2.7.1) (روبوت إضافة: [[uk:Протести в арабсько...  NaN  الربيع العربي   
4    روبوت: قوالب الصيانة؛ +[[قالب:يتيمة|{{يتيمة}}]]  NaN  الربيع العربي   

         date  diff     lag       age  
0  2011-02-01   NaN     NaN  0.000000  
1  2011-02-01   6.0    38.0  0.000440  
2  2011-02-01  39.0   271.0  0.003576  
3  2011-02-01  73.0  3276.0  0.041493  
4  2011-02-01  44.0  1061.0  0.053773

In [26]:
#this is numbers so it shoudl be fine
ar_freq_revids = ar_rev_df.groupby(pd.Grouper(key='timestamp',freq='M')).agg({'revid':'min'})['revid']
ar_freq_revids = ar_freq_revids.dropna()


ar_outlinks = {}

for _revid in ar_freq_revids.values:
    #print(_revid)
    ar_outlinks[_revid] = wf.get_revision_outlinks(int(_revid), endpoint='ar.wikipedia.org/w/api.php')

In [27]:
ar_freq_revids

timestamp
2011-02-28 00:00:00+00:00     6345923.0
2011-03-31 00:00:00+00:00     6459075.0
2011-04-30 00:00:00+00:00     6602258.0
2011-05-31 00:00:00+00:00     6758727.0
2011-06-30 00:00:00+00:00     6911767.0
                                ...    
2023-06-30 00:00:00+00:00    62699194.0
2023-07-31 00:00:00+00:00    63391950.0
2023-08-31 00:00:00+00:00    63619143.0
2023-09-30 00:00:00+00:00    64206689.0
2023-10-31 00:00:00+00:00    64997097.0
Name: revid, Length: 144, dtype: float64

In [28]:
#resolve redirects

for i in ar_outlinks:
    ar_outlinks[i] = wf.resolve_redirects(ar_outlinks[i], endpoint='ar.wikipedia.org/w/api.php')
#     print(outlinks[i])

In [29]:
import pickle

with open('02c_ar_as_rev_outlinks_m.pkl', 'wb') as f:
    pickle.dump(ar_outlinks, f)

In [30]:
with open('02c_ar_as_rev_time_m.pkl', 'wb') as f:
    pickle.dump(ar_freq_revids, f)

## make binary outlinks df

In [31]:
with open("02c_ar_as_rev_outlinks_m.pkl", 'rb') as pickleFile:
    ar_outlinks = pickle.load(pickleFile)

In [32]:
#make a unique outlinks dict

ar_outlinksUnique = {}
keys = ar_outlinks.keys()

for i in keys:
    ar_outlinksUnique[i] = np.unique(ar_outlinks[i]).tolist()

In [33]:
#make list of all of the unique outlinks used througout time
#this is only a list of outlinks to be later used for the df and heat map

ar_everyOutlink = merge(ar_outlinks.values()) #makes lists of lists
ar_everyOutlink = list(itertools.chain.from_iterable(ar_everyOutlink)) #puts them all in one list
ar_everyOutlink = np.unique(ar_everyOutlink).tolist() #a list of alphabetized unique outlinks

len(ar_everyOutlink)

326

In [34]:
#go through and create a new dictionary with ones and values correlating to everyOutlink

ar_binaryRevOutlinkDict = {}
keys = ar_outlinksUnique.keys()

for rev in keys:
    ar_binaryRevOutlinkDict[rev] = [1 if r in ar_outlinksUnique[rev] else 0 for r in ar_everyOutlink]


In [35]:
#make a df with everything

#make a df
ar_df = pd.DataFrame.from_dict(ar_binaryRevOutlinkDict, orient='index', columns=ar_everyOutlink )
ar_df.reset_index(inplace=True) #make the revision ids a column 

#change name
names = ar_df.columns.tolist()
names[names.index('index')] = 'revs_id'
ar_df.columns = names

ar_df.head()

revs_id  1 أغسطس  1 فبراير  11 فبراير  12 مايو  13 أبريل  14 يناير  \
0  6345923.0        0         0          0        0         0         0   
1  6459075.0        0         1          1        0         0         1   
2  6602258.0        0         0          1        0         0         1   
3  6758727.0        0         0          1        0         0         1   
4  6911767.0        0         0          1        1         1         1   

   1432 هـ  15 أبريل  15 مارس  ...  هضبة الجولان  وائل غنيم  واشنطن العاصمة  \
0        0         0        0  ...             0          0               0   
1        1         0        0  ...             0          1               0   
2        1         0        1  ...             0          1               0   
3        1         0        1  ...             0          1               0   
4        1         1        1  ...             0          1               0   

   وحدة عربية  وزارة الداخلية  وزارة الداخلية (مصر)  ويكيبيديا:بحاجة لمصدر  \
0           0               0                     0                      0   
1           0               1                     0                      0   
2           0               0                     0                      0   
3           0               0                     0                      0   
4           1               0                     1                      1   

   ويكيبيديا:دليل الأسلوب/تجنب التعابير المبهمة  ويكيليكس  يوتيوب  
0                                             0         0       0  
1                                             0         0       1  
2                                             0         1       1  
3                                             0         1       1  
4                                             0         1       1  

[5 rows x 327 columns]

In [37]:
#clean up timestamp information
times = ar_freq_revids.index

times = times.date #making it so its just the date

ar_df['timestamp'] = times #add the timestamps
ar_df['timestamp'] = pd.to_datetime(ar_df['timestamp']) #stuff you have to do bc its a different format
ar_df.set_index("timestamp", inplace=True, drop=True)


ar_df.head()

revs_id  1 أغسطس  1 فبراير  11 فبراير  12 مايو  13 أبريل  \
timestamp                                                                
2011-02-28  6345923.0        0         0          0        0         0   
2011-03-31  6459075.0        0         1          1        0         0   
2011-04-30  6602258.0        0         0          1        0         0   
2011-05-31  6758727.0        0         0          1        0         0   
2011-06-30  6911767.0        0         0          1        1         1   

            14 يناير  1432 هـ  15 أبريل  15 مارس  ...  هضبة الجولان  \
timestamp                                         ...                 
2011-02-28         0        0         0        0  ...             0   
2011-03-31         1        1         0        0  ...             0   
2011-04-30         1        1         0        1  ...             0   
2011-05-31         1        1         0        1  ...             0   
2011-06-30         1        1         1        1  ...             0   

            وائل غنيم  واشنطن العاصمة  وحدة عربية  وزارة الداخلية  \
timestamp                                                           
2011-02-28          0               0           0               0   
2011-03-31          1               0           0               1   
2011-04-30          1               0           0               0   
2011-05-31          1               0           0               0   
2011-06-30          1               0           1               0   

            وزارة الداخلية (مصر)  ويكيبيديا:بحاجة لمصدر  \
timestamp                                                 
2011-02-28                     0                      0   
2011-03-31                     0                      0   
2011-04-30                     0                      0   
2011-05-31                     0                      0   
2011-06-30                     1                      1   

            ويكيبيديا:دليل الأسلوب/تجنب التعابير المبهمة  ويكيليكس  يوتيوب  
timestamp                                                                   
2011-02-28                                             0         0       0  
2011-03-31                                             0         0       1  
2011-04-30                                             0         1       1  
2011-05-31                                             0         1       1  
2011-06-30                                             0         1       1  

[5 rows x 327 columns]

In [38]:
#get rid of revision ids and transpose, switching the axes makes the heat map easier to read
ar_data = ar_df.iloc[: , 1:] #drop revs_id

ar_data = ar_data.transpose() #flip
ar_data.index.name = None

ar_data.head()

timestamp  2011-02-28  2011-03-31  2011-04-30  2011-05-31  2011-06-30  \
1 أغسطس             0           0           0           0           0   
1 فبراير            0           1           0           0           0   
11 فبراير           0           1           1           1           1   
12 مايو             0           0           0           0           1   
13 أبريل            0           0           0           0           1   

timestamp  2011-07-31  2011-08-31  2011-09-30  2011-10-31  2011-11-30  ...  \
1 أغسطس             0           0           0           0           0  ...   
1 فبراير            0           0           0           0           0  ...   
11 فبراير           1           1           1           1           1  ...   
12 مايو             1           1           1           1           1  ...   
13 أبريل            1           1           1           1           1  ...   

timestamp  2022-11-30  2022-12-31  2023-01-31  2023-02-28  2023-03-31  \
1 أغسطس             1           1           1           1           1   
1 فبراير            0           0           0           0           0   
11 فبراير           1           1           1           1           1   
12 مايو             1           1           1           1           1   
13 أبريل            1           1           1           1           1   

timestamp  2023-06-30  2023-07-31  2023-08-31  2023-09-30  2023-10-31  
1 أغسطس             1           1           1           1           1  
1 فبراير            0           0           0           0           0  
11 فبراير           1           1           1           1           1  
12 مايو             1           1           1           1           1  
13 أبريل            1           1           1           1           1  

[5 rows x 144 columns]

In [39]:
with open('02c_outlinkInclusiondf_ar.pkl', 'wb') as f:
    pickle.dump(ar_data, f)

In [70]:
with open('02c_outlinkInclusiondf_ar.pkl', 'rb') as pickleFile:
    arDF = pickle.load(pickleFile)

In [75]:
arDF2 = arDF.transpose()

In [76]:
arDF2.head

<bound method NDFrame.head of             1 أغسطس  1 فبراير  11 فبراير  12 مايو  13 أبريل  14 يناير  \
timestamp                                                               
2011-02-28        0         0          0        0         0         0   
2011-03-31        0         1          1        0         0         1   
2011-04-30        0         0          1        0         0         1   
2011-05-31        0         0          1        0         0         1   
2011-06-30        0         0          1        1         1         1   
2011-07-31        0         0          1        1         1         1   
2011-08-31        0         0          1        1         1         1   
2011-09-30        0         0          1        1         1         1   
2011-10-31        0         0          1        1         1         1   
2011-11-30        0         0          1        1         1         1   
2011-12-31        0         0          1        1         1         1   
2012-01-31        0  

In [79]:
arDF2['الجيش السوري الحر']

timestamp
2011-02-28    0
2011-03-31    0
2011-04-30    0
2011-05-31    0
2011-06-30    0
2011-07-31    0
2011-08-31    0
2011-09-30    0
2011-10-31    0
2011-11-30    0
2011-12-31    0
2012-01-31    0
2012-02-29    0
2012-03-31    0
2012-04-30    0
2012-05-31    0
2012-06-30    0
2012-07-31    0
2012-08-31    0
2012-09-30    1
2012-10-31    1
2012-11-30    1
2012-12-31    1
2013-01-31    1
2013-02-28    1
2013-03-31    1
2013-04-30    1
2013-05-31    1
2013-06-30    1
2013-07-31    1
2013-08-31    1
2013-09-30    1
2013-10-31    1
2013-11-30    1
2013-12-31    0
2014-01-31    0
2014-02-28    1
2014-03-31    1
2014-04-30    1
2014-05-31    1
2014-06-30    1
2014-07-31    1
2014-08-31    1
2014-09-30    1
2014-10-31    1
2014-11-30    1
2014-12-31    1
2015-01-31    1
2015-02-28    1
2015-03-31    1
2015-04-30    1
2015-05-31    1
2015-06-30    1
2015-07-31    1
2015-08-31    1
2015-09-30    1
2015-10-31    1
2015-11-30    1
2015-12-31    1
2016-01-31    1
2016-02-29    1
2016-03-31    

In [80]:
lyst = ['بوابة:العرب', 'موسوعة ستانفورد للفلسفة', 'احتجاجات جنوب العراق 2018', 'حيدر العبادي', 'الثورة السودانية', 'بوابة:آسيا', 'بوابة:علم الاجتماع', 'رئيس مجلس الوزراء (مصر)', 'بوابة:مجتمع', 'عمر البشير', 'مجلس الوزراء المصري', 'منظمة العفو الدولية', 'استقلال القضاء', 'الاحتجاجات البحرينية 2011', 'حرية التعبير', 'مساواة اجتماعية', 'المحكمة الجنائية الدولية', '1978', 'الكويت', 'مجلس الأمة الكويتي', 'ناصر المحمد الأحمد الصباح', 'الحزب الوطني الديمقراطي (مصر)', '20 أكتوبر', '2012', 'الاحتجاجات الأردنية 2011–2012', 'الاحتجاجات الجزائرية 2011', 'الاحتجاجات الجيبوتية 2011', 'الاحتجاجات السعودية 2011–2013', 'الاحتجاجات العراقية 2011', 'الاحتجاجات العمانية 2011', 'الاحتجاجات الفلسطينية لإنهاء الانقسام', 'الاحتجاجات الكويتية 2011', 'الاحتجاجات اللبنانية 2011', 'الاحتجاجات المغربية 2011', 'الاحتجاجات الموريتانية 2011–12', 'الباجي قائد السبسي', 'الحرب الأهلية السورية', 'الحرب الأهلية الليبية (2011)', 'المبادرة الخليجية', 'المجلس الوطني الانتقالي (توضيح)', 'عبد ربه منصور هادي', 'قانون الطوارئ في سوريا', 'محاكمة حسني مبارك', 'معركة سرت (توضيح)', 'مقتل معمر القذافي', 'هالة المصراتي', 'بوابة:ثورات الربيع العربي', 'جدة', 'الجيش السوري الحر', 'المجلس الأعلى للقوات المسلحة (مصر)', 'رويترز', 'سيف الإسلام القذافي', 'طرابلس', 'محمد القذافي', 'أحمد علي عبد الله صالح', 'انقلاب 1969 في ليبيا', 'ثورة الشباب اليمنية', 'حافظ الأسد', 'سيدي بوزيد (توضيح)', 'ملكية دستورية', 'البيضاء (ليبيا)', 'الاحتجاجات السودانية 2011', '15 مارس', '15 مايو', '17 فبراير', '18 يناير', '27 فبراير', '29 مارس', 'الانقسام الفلسطيني', 'الضفة الغربية', 'النكبة', 'بغداد', 'جامعة الدول العربية', 'حرب 1948', 'حركة 20 فبراير', 'حركة حماس', 'حركة فتح', 'حصار غزة', 'فلسطين', 'فلسطينيون', 'قرار حق العودة للاجئين الفلسطينيين', 'قطاع غزة', 'معمر القذافي', '12 مايو', '13 أبريل', '15 أبريل', '16 أبريل', '17 مايو', '18 فبراير', '21 فبراير', '22 فبراير', '24 مايو', '26 مارس', '28 فبراير', '5 مارس', '5 مايو', '8 مايو', '9 أبريل', 'أحمد المغربي', 'أحمد عز (توضيح)', 'أحمد فتحي سرور', 'أنس الفقي', 'الأهواز', 'الحميدية (توضيح)', 'الشرطة المصرية', 'الشعب يريد إسقاط النظام', 'القاهرة', 'المملكة المتحدة', 'برلمان المملكة المتحدة', 'جمال مبارك', 'جنيه مصري', 'حادث كنيسة القديسين', 'حبيب العادلي', 'دواء', 'زكريا عزمي', 'زهير جرانة', 'سفينة بضائع', 'سوزان مبارك', 'صفوت الشريف', 'طعام', 'عبد الله بن عبد العزيز آل سعود', 'قومية عربية', 'لندن', 'مجلس النواب البحريني', 'مظاهرات الحدود الإسرائيلية 2011', 'نائب عام', 'وحدة عربية', 'وزارة الداخلية (مصر)', 'ويكيبيديا:بحاجة لمصدر', '3 مارس', 'إقليم الأهواز', 'الحرس الثوري الإيراني', 'الخفاجية (توضيح)', 'فورين بوليسي', 'ماء', 'مستشفى', '11 فبراير', '14 يناير', '1432 هـ', '15 يناير', '17 ديسمبر', '18 ديسمبر', '1946', '1975', '1990', '2003', '2010', '2011', '2014', '24 صفر', '25 يناير', '4 يناير', 'إسرائيل', 'إنترنت', 'الانتداب الفرنسي على لبنان', 'الحرب الأهلية اللبنانية', 'السعودية', 'الشرق الأوسط', 'المؤتمر القومي العربي', 'المجلس الدستوري للجمهورية (تونس)', 'الولايات المتحدة', 'بشار الأسد', 'ثورة 25 يناير', 'جيبوتي', 'حركة شباب 6 أبريل', 'حسني مبارك', 'خط الفقر', 'دستور تونس (توضيح)', 'دميتري ميدفيديف', 'روسيا', 'زين العابدين بن علي', 'سوريا', 'علمانية', 'علي عبد الله صالح', 'عمر سليمان', 'عيد الشرطة (مصر)', 'غزو العراق', 'فؤاد المبزع', 'فيسبوك', 'قانون الطوارئ', 'مجلس النواب (تونس)', 'محمد الغنوشي', 'وائل غنيم', 'يوتيوب', 'محمد الغنوشي', 'الأردن', 'الثورة التونسية', 'الوطن العربي', 'تونس', 'لبنان', 'ليبيا', 'محمد البوعزيزي', 'مصر', 'وائل غنيم', '29 يناير', 'الإخوان المسلمون', 'محمد مرسي', 'سبتمبر', 'جسر الملك حسين', 'رئيس الوزراء', 'هضبة الجولان', 'انقلاب 2013 في مصر', 'عبد الفتاح السيسي', 'مظاهرات 30 يونيو 2013 في مصر', 'بنيامين نتنياهو', 'هضبة الجولان', 'بوابة:إفريقيا', 'بوابة:السياسة', 'بوابة:الوطن العربي', 'بوابة:عقد 2010', 'اقتصاد (علم)', 'بطالة', 'بوابة:الشرق الأوسط', 'رئيس مصر', 'صلاة الجمعة', 'فساد', 'كانون الثاني', 'الكيان الصهيوني', 'درعا', 'برنارد لويس', '18 مارس', 'الإخوان المسلمون']

In [81]:
arDF3 = pd.DataFrame()
for i in lyst:
    extracted_col = arDF2[i]
    arDF3 = pd.concat([arDF3, extracted_col.rename(i)], axis=1)

In [90]:
pd.set_option('display.max_columns', None)

arDF3.head()

بوابة:العرب  موسوعة ستانفورد للفلسفة  \
2011-02-28 00:00:00            0                        0   
2011-03-31 00:00:00            0                        0   
2011-04-30 00:00:00            0                        0   
2011-05-31 00:00:00            0                        0   
2011-06-30 00:00:00            0                        0   

                     احتجاجات جنوب العراق 2018  حيدر العبادي  \
2011-02-28 00:00:00                          0             0   
2011-03-31 00:00:00                          0             0   
2011-04-30 00:00:00                          0             0   
2011-05-31 00:00:00                          0             0   
2011-06-30 00:00:00                          0             0   

                     الثورة السودانية  بوابة:آسيا  بوابة:علم الاجتماع  \
2011-02-28 00:00:00                 0           0                   0   
2011-03-31 00:00:00                 0           0                   0   
2011-04-30 00:00:00                 0           0                   0   
2011-05-31 00:00:00                 0           0                   0   
2011-06-30 00:00:00                 0           0                   0   

                     رئيس مجلس الوزراء (مصر)  بوابة:مجتمع  عمر البشير  \
2011-02-28 00:00:00                        0            0           0   
2011-03-31 00:00:00                        0            0           0   
2011-04-30 00:00:00                        0            0           0   
2011-05-31 00:00:00                        0            0           0   
2011-06-30 00:00:00                        0            0           0   

                     مجلس الوزراء المصري  منظمة العفو الدولية  استقلال القضاء  \
2011-02-28 00:00:00                    0                    0               0   
2011-03-31 00:00:00                    0                    0               0   
2011-04-30 00:00:00                    0                    0               0   
2011-05-31 00:00:00                    0                    0               0   
2011-06-30 00:00:00                    1                    0               0   

                     الاحتجاجات البحرينية 2011  حرية التعبير  مساواة اجتماعية  \
2011-02-28 00:00:00                          0             0                0   
2011-03-31 00:00:00                          0             0                0   
2011-04-30 00:00:00                          0             0                0   
2011-05-31 00:00:00                          0             0                0   
2011-06-30 00:00:00                          0             0                0   

                     المحكمة الجنائية الدولية  1978  الكويت  \
2011-02-28 00:00:00                         0     0       0   
2011-03-31 00:00:00                         0     0       0   
2011-04-30 00:00:00                         0     0       0   
2011-05-31 00:00:00                         0     0       0   
2011-06-30 00:00:00                         0     0       0   

                     مجلس الأمة الكويتي  ناصر المحمد الأحمد الصباح  \
2011-02-28 00:00:00                   0                          0   
2011-03-31 00:00:00                   0                          0   
2011-04-30 00:00:00                   0                          0   
2011-05-31 00:00:00                   0                          0   
2011-06-30 00:00:00                   0                          0   

                     الحزب الوطني الديمقراطي (مصر)  20 أكتوبر  2012  \
2011-02-28 00:00:00                              0          0     0   
2011-03-31 00:00:00                              0          0     0   
2011-04-30 00:00:00                              0          0     0   
2011-05-31 00:00:00                              0          0     0   
2011-06-30 00:00:00                              0          0     0   

                     الاحتجاجات الأردنية 2011–2012  الاحتجاجات الجزائرية 2011  \
2011-02-28 00:00:00                              0                          0   
2011-03-31 00:00:00         

In [93]:
# len(lyst)

arDF3['رئيس مصر']

2011-02-28 00:00:00    0
2011-03-31 00:00:00    0
2011-04-30 00:00:00    0
2011-05-31 00:00:00    0
2011-06-30 00:00:00    0
2011-07-31 00:00:00    0
2011-08-31 00:00:00    0
2011-09-30 00:00:00    0
2011-10-31 00:00:00    0
2011-11-30 00:00:00    0
2011-12-31 00:00:00    0
2012-01-31 00:00:00    0
2012-02-29 00:00:00    0
2012-03-31 00:00:00    0
2012-04-30 00:00:00    0
2012-05-31 00:00:00    0
2012-06-30 00:00:00    0
2012-07-31 00:00:00    0
2012-08-31 00:00:00    0
2012-09-30 00:00:00    0
2012-10-31 00:00:00    0
2012-11-30 00:00:00    0
2012-12-31 00:00:00    0
2013-01-31 00:00:00    0
2013-02-28 00:00:00    0
2013-03-31 00:00:00    0
2013-04-30 00:00:00    0
2013-05-31 00:00:00    0
2013-06-30 00:00:00    0
2013-07-31 00:00:00    0
2013-08-31 00:00:00    0
2013-09-30 00:00:00    0
2013-10-31 00:00:00    0
2013-11-30 00:00:00    0
2013-12-31 00:00:00    0
2014-01-31 00:00:00    0
2014-02-28 00:00:00    0
2014-03-31 00:00:00    0
2014-04-30 00:00:00    0
2014-05-31 00:00:00    0


In [103]:
lyst2 = ['1 أغسطس', '20 فبراير', 'أحزاب سياسية في المغرب', 'المغرب', 'بوابة:عقد 2000', 'بوابة:عقد 2020', 'تواصل اجتماعي', 'دستور المغرب', 'محكمة العدل الدولية', 'بوابة:عصور حديثة', 'عبد العزيز بوتفليقة', 'الجزائر', '1 فبراير', '16 يناير', '22 يناير', '28 يناير', '5 فبراير', '6 يناير', 'البحرين', 'الجزائر (مدينة)', 'الحريقة (توضيح)', 'الرياض', 'العوامية', 'القوات المسلحة السورية', 'بنغازي', 'بيروت', 'حزب الأمة الإسلامي', 'حفر الباطن', 'حلب', 'دمشق', 'سمير الرفاعي', 'سيول جدة 2011', 'شارع الأمير محمد بن عبد العزيز (جدة)', 'شرطة', 'عين الحجل', 'كرد', 'محسن بوطرفيف', 'هاتف محمول', 'وزارة الداخلية', 'اليمن', 'نجيب ميقاتي', 'أوغندا', 'إثيوبيا', 'الشباب (تنظيم صومالي)', 'حلف شمال الأطلسي', 'كيسمايو', 'كينيا', 'مقديشو', 'منظمة العمل الدولية', '2008', 'العصور الوسطى', 'تويتر', 'ويكيليكس', '30 يناير', 'حسن مشيمع', 'القوات المسلحة المصرية', 'ويكيبيديا:دليل الأسلوب/تجنب التعابير المبهمة', 'الإمارات العربية المتحدة', 'جزر القمر', 'قطر', '17 مارس', '3 فبراير', 'أن تكون عربيا في أيامنا (كتاب)', 'عزمي بشارة', 'المحيط الأطلسي', 'حرية', 'الخليج العربي', 'جمعة الكرامة', 'علي محسن الأحمر', 'قبائل اليمن', '30 يونيو', 'الاتحاد السوفيتي']

In [104]:
# , 'احتجاجات الجزائر 2019'
arDF4 = pd.DataFrame()
for i in lyst2:
    extracted_col = arDF2[i]
    arDF4 = pd.concat([arDF4, extracted_col.rename(i)], axis=1)

In [107]:
arDF4

1 أغسطس  20 فبراير  أحزاب سياسية في المغرب  المغرب  \
2011-02-28 00:00:00        0          0                       0       0   
2011-03-31 00:00:00        0          0                       0       0   
2011-04-30 00:00:00        0          0                       0       0   
2011-05-31 00:00:00        0          0                       0       0   
2011-06-30 00:00:00        0          0                       0       0   
2011-07-31 00:00:00        0          0                       0       0   
2011-08-31 00:00:00        0          0                       0       0   
2011-09-30 00:00:00        0          0                       0       0   
2011-10-31 00:00:00        0          0                       0       0   
2011-11-30 00:00:00        0          0                       0       0   
2011-12-31 00:00:00        0          0                       0       0   
2012-01-31 00:00:00        0          0                       0       0   
2012-02-29 00:00:00        0          0                       0       0   
2012-03-31 00:00:00        0          0                       0       0   
2012-04-30 00:00:00        0          0                       0       0   
2012-05-31 00:00:00        0          0                       0       0   
2012-06-30 00:00:00        0          0                       0       0   
2012-07-31 00:00:00        0          0                       0       0   
2012-08-31 00:00:00        0          0                       0       0   
2012-09-30 00:00:00        0          0                       0       0   
2012-10-31 00:00:00        0          0                       0       0   
2012-11-30 00:00:00        0          0                       0       0   
2012-12-31 00:00:00        0          0                       0       0   
2013-01-31 00:00:00        0          0                       0       0   
2013-02-28 00:00:00        0          0                       0       0   
2013-03-31 00:00:00        0          0                       0       0   
2013-04-30 00:00:00        0          0                       0       0   
2013-05-31 00:00:00        0          0                       0       0   
2013-06-30 00:00:00        0          0                       0       0   
2013-07-31 00:00:00        0          0                       0       0   
2013-08-31 00:00:00        0          0                       0       0   
2013-09-30 00:00:00        0          0                       0       0   
2013-10-31 00:00:00        0          0                       0       0   
2013-11-30 00:00:00        0          0                       0       0   
2013-12-31 00:00:00        0          0                       0       0   
2014-01-31 00:00:00        0          0                       0       0   
2014-02-28 00:00:00        0          0                       0       0   
2014-03-31 00:00:00        0          0                       0       0   
2014-04-30 00:00:00        0          0                       0       0   
2014-05-31 00:00:00        0          0                       0       0   
2014-06-30 00:00:00        0          0                       0       0   
2014-07-31 00:00:00        0          0                       0       0   
2014-08-31 00:00:00        0          0                       0       0   
2014-09-30 00:00:00        0          0                       0       0   
2014-10-31 00:00:00        0          0                       0       0   
2014-11-30 00:00:00        0          0                       0       0   
2014-12-31 00:00:00        0          0                       0       0   
2015-01-31 00:00:00        0          0                       0       0   
2015-02-28 00:00:00        0          0                       0       0   
2015-03-31 00:00:00        0          0                       0       0   
2015-04-30 00:00:00        0          0                       0       0   
2015-05-31 00:00:00        0          0                       0       0   
2015-06-30 00:00:00        0          0       

In [125]:
start_date = pd.to_datetime('2022-02-28')
end_date = pd.to_datetime('2023-08-31')


# Select DataFrame rows between two dates
mask = (arDF4.index > start_date) & (arDF4.index <= end_date)
arDF5 = arDF4.loc[mask]

In [126]:
arDF5

1 أغسطس  20 فبراير  أحزاب سياسية في المغرب  المغرب  \
2022-03-31 00:00:00        1          1                       1       1   
2022-04-30 00:00:00        1          1                       1       1   
2022-05-31 00:00:00        1          1                       1       1   
2022-06-30 00:00:00        1          1                       1       1   
2022-07-31 00:00:00        1          1                       1       1   
2022-08-31 00:00:00        1          1                       1       1   
2022-09-30 00:00:00        1          1                       1       1   
2022-10-31 00:00:00        1          1                       1       1   
2022-11-30 00:00:00        1          1                       1       1   
2022-12-31 00:00:00        1          1                       1       1   
2023-01-31 00:00:00        1          1                       1       1   
2023-02-28 00:00:00        1          1                       1       1   
2023-03-31 00:00:00        1          1                       1       1   
2023-06-30 00:00:00        1          1                       1       1   
2023-07-31 00:00:00        1          1                       1       1   
2023-08-31 00:00:00        1          1                       1       1   

                     بوابة:عقد 2000  بوابة:عقد 2020  تواصل اجتماعي  \
2022-03-31 00:00:00               1               1              1   
2022-04-30 00:00:00               1               1              1   
2022-05-31 00:00:00               1               1              1   
2022-06-30 00:00:00               1               1              1   
2022-07-31 00:00:00               1               1              1   
2022-08-31 00:00:00               1               1              1   
2022-09-30 00:00:00               1               1              1   
2022-10-31 00:00:00               1               1              1   
2022-11-30 00:00:00               1               1              1   
2022-12-31 00:00:00               1               1              1   
2023-01-31 00:00:00               1               1              1   
2023-02-28 00:00:00               1               1              1   
2023-03-31 00:00:00               1               1              1   
2023-06-30 00:00:00               1               1              1   
2023-07-31 00:00:00               1               1              1   
2023-08-31 00:00:00               1               1              1   

                     دستور المغرب  محكمة العدل الدولية  بوابة:عصور حديثة  \
2022-03-31 00:00:00             1                    1                 1   
2022-04-30 00:00:00             1                    1                 1   
2022-05-31 00:00:00             1                    1                 1   
2022-06-30 00:00:00             1                    1                 1   
2022-07-31 00:00:00             1                    1                 1   
2022-08-31 00:00:00             1                    1                 1   
2022-09-30 00:00:00             1                    1                 1   
2022-10-31 00:00:00             1                    1                 1   
2022-11-30 00:00:00             1                    1                 1   
2022-12-31 00:00:00             1                    1                 1   
2023-01-31 00:00:00             1                    1                 1   
2023-02-28 00:00:00             1                    1                 1   
2023-03-31 00:00:00             1                    1                 1   
2023-06-30 00:00:00             1                    1                 1   
2023-07-31 00:00:00             1                    1                 1   
2023-08-31 00:00:00             1                    1                 1   

                     عبد العزيز بوتفليقة  الجزائر  1 فبراير  16 يناير  \
2022-03-31 00:00:00                    0        0         0         0   
2022-04-30 00:00:00                    0        0         0         0   
2022-05-31 00:00:00                    0  